# Burgers' Equation

We will solve a Burgers' equation:

$$
\frac{\partial u}{\partial t} + u\frac{\partial u}{\partial x} = v\frac{\partial^2 u}{\partial x^2}, \qquad \text{where} \quad x  \in [-1,1],  \quad t \in [0,1],
$$

with the Dirichlet boundary conditions and the initial condition:

$$
u(-1,t) = u(1,t) = 0, \qquad u(x,0) = -sin(\pi x)
$$

and using $v = 0.01/\pi$.

The reference solution is computed by finite differences *here*.

## Implementation and Training

First, we import the libraries:

In [9]:
import torch
import torch.nn as nn
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
import datetime
import math
from IPython.display import HTML

We set the value of v, the value of $\pi$, define the $sine$ function and the maximum and minimum values of the x domain:

In [10]:
sin = torch.sin
pi = math.pi
v=0.01/pi

x_min = -1.
x_max = 1.

Now, we set the parameters of the neural network: it has a structure with 2 input ($x, t$) and 1 output ($u(x,t)$), 5000 maximum training steps, 2 hidden layers with 32 neurons each, 100 samples and a target minimum loss value of $10^{-4}$.

In [11]:
inputs = 2
outputs = 1
hn_1 = 32
hn_2 = 32
steps = 0
max_steps = 15000
loss = 10
min_loss = 1e-4
log_each = 500
samples = 100
loss_values = []

In this part, we define a new class implementing the activation function $sin(x)$, due to the oscillatory nature of the solution.

In [12]:
class Sine(nn.Module):
    def __init__(self):
        super().__init__()
    def forward(self, x):
        return torch.sin(x)

The multilayer perceptron (MLP) structure is:

In [13]:
mlp = nn.Sequential(
    nn.Linear(inputs,hn_1),
    Sine(),
    nn.Linear(hn_1, hn_2),
    Sine(),
    nn.Linear(hn_2, outputs)
)

optimizer = torch.optim.Adam(mlp.parameters())
criterion = nn.MSELoss()
mlp.train()

Sequential(
  (0): Linear(in_features=2, out_features=32, bias=True)
  (1): Sine()
  (2): Linear(in_features=32, out_features=32, bias=True)
  (3): Sine()
  (4): Linear(in_features=32, out_features=1, bias=True)
)

In this section, we define a function that calculates the gradients.

In [14]:
def computeGrads(y, x):
    grads, = torch.autograd.grad(y, x, grad_outputs=y.data.new(y.shape).fill_(1), create_graph=True, only_inputs=True)
    return grads

Next, we define the main training loop and the timer:

In [15]:
starttime_train = datetime.datetime.now()
print('----Training Started----')

while steps < max_steps and loss > min_loss:
    x = (x_max - x_min)*torch.rand(samples) + x_min
    t = torch.rand(samples)
    X = torch.stack([x, t], axis=-1)
    X.requires_grad = True
    Y = mlp(X)
    grads = computeGrads(Y, X)
    dudx = grads[:, :1]
    dudt = grads[:, 1:]
    grads2 = computeGrads(dudx, X)
    d2udx2 = grads2[:, :1]
    ode_loss = criterion(dudt, -Y*dudx -v*d2udx2)

    #initial condition
    x = (x_max - x_min)*torch.rand(samples) + x_min
    t_0 = torch.zeros(samples)
    X_initial = torch.stack([x, t_0], axis=-1)
    Y_initial = mlp(X_initial)
    u_initial = -sin(pi*x).unsqueeze(1)
    ic_loss = criterion(Y_initial, u_initial)

    #boundary conditions x=-1
    x_1 = -torch.ones(samples)
    t = torch.rand(samples)
    X_boundary_1 = torch.stack([x_1, t], axis=-1)
    Y_boundary_1 = mlp(X_boundary_1)
    zero = torch.zeros(samples, 1)
    bc_1_loss = criterion(Y_boundary_1, zero)
    
    #boundary conditions x=1
    x1 = torch.ones(samples)
    X_boundary1 = torch.stack([x1, t], axis=-1)
    Y_boundary1 = mlp(X_boundary1)
    bc1_loss = criterion(Y_boundary1, zero)

    bc_loss = bc_1_loss + bc1_loss

    optimizer.zero_grad()
    loss = ode_loss + ic_loss  + bc_loss
    loss.backward()
    optimizer.step()

    loss_values.append(loss.detach().numpy())

    if steps % log_each == 0:
        print(f'Step:{steps}| ode_loss {ode_loss.item():.5f} ic_loss {ic_loss.item():.5f} bc_loss {bc_loss.item():.5f}')

    steps+=1

endtime_train = datetime.datetime.now()
train_time = endtime_train - starttime_train
train_time_formatted = train_time.seconds + train_time.microseconds / 1e6
print('---Training Finished---')

print(f'Training Duration: {steps} steps in {train_time_formatted:.3f} seconds')

----Training Started----
Step:0| ode_loss 0.00130 ic_loss 0.78671 bc_loss 0.23445
Step:500| ode_loss 0.05696 ic_loss 0.10145 bc_loss 0.00578
Step:1000| ode_loss 0.05785 ic_loss 0.09795 bc_loss 0.00524
Step:1500| ode_loss 0.06802 ic_loss 0.09766 bc_loss 0.00478
Step:2000| ode_loss 0.07032 ic_loss 0.07652 bc_loss 0.00631
Step:2500| ode_loss 0.05895 ic_loss 0.07792 bc_loss 0.00262
Step:3000| ode_loss 0.04520 ic_loss 0.07420 bc_loss 0.00150
Step:3500| ode_loss 0.04378 ic_loss 0.08935 bc_loss 0.00115
Step:4000| ode_loss 0.04267 ic_loss 0.08689 bc_loss 0.00089
Step:4500| ode_loss 0.05377 ic_loss 0.06686 bc_loss 0.00104
Step:5000| ode_loss 0.06460 ic_loss 0.07401 bc_loss 0.00114
Step:5500| ode_loss 0.06153 ic_loss 0.05536 bc_loss 0.00090
Step:6000| ode_loss 0.05316 ic_loss 0.07990 bc_loss 0.00112
Step:6500| ode_loss 0.04373 ic_loss 0.07492 bc_loss 0.00174
Step:7000| ode_loss 0.04454 ic_loss 0.07664 bc_loss 0.00116
Step:7500| ode_loss 0.05679 ic_loss 0.05922 bc_loss 0.00101
Step:8000| ode_loss

KeyboardInterrupt: 

## Visualization

To visualize model solution, we obtain the output of the trained model and display it as a gif.

In [ ]:
x = np.linspace(x_min, x_max, samples)
t = np.linspace(0, 1, samples)

u = [] 
time = []

for t_ in t:
    with torch.no_grad():
        X = torch.stack([torch.from_numpy(x).float(), torch.ones(samples)*t_], axis=-1)
        Y = mlp(X)
    u.append(Y.detach().numpy())
    time.append(t_)

def update(i):
    ax.clear()
    ax.plot(x, u[i])
    ax.set_xlabel('$x$')
    ax.set_ylabel('$u$')
    ax.set_title(f'$t = {time[i]:.3f}$')
    ax.set_ylim(-1,1)
    ax.grid(True)
    return ax

fig = plt.figure(dpi=100)
ax = plt.subplot(1,1,1)
anim = animation.FuncAnimation(fig, update, frames=len(u), interval=200)
plt.close(fig)
HTML(anim.to_jshtml())